## 💼 "All-Weather" Risk-Parity Portfolio Framework

### 📥 Setups and ETFs Selection

Installation and Import of required packages

In [295]:
# !pip install -r requirements.txt

In [296]:
import yfinance as yf
import pandas as pd
import numpy as np
import plotly.graph_objects as go

Initialization of portfolio parameters

In [297]:
TICKERS: list[str] = ['SPY', 'TLT', 'GLD', 'TIP', 'BIL']  # Equities, Fixed Income, Commodities, Inflation-protected, Cash
START_DATE: str = '2015-01-01'
END_DATE: str = '2025-06-27'
VOL_LOOKBACK: int = 126  # Volatility Lookback Period Length

### 🏗️ Data Download

Function for fetching daily price data

In [298]:
def get_etf_data(tickers: list[str], start: str, end: str):
    """
    Fetches financial data from Yahoo Finance API for given tickers and date range.
    
    Parameters:
        tickers (list[str]): U.S. equity ticker symbols
        start_date (str): Start date in 'YYYY-MM-DD' format
        end_date (str): End date in 'YYYY-MM-DD' format

    Returns:
        pd.DataFrame: DataFrame with date-indexed adjusted closing price data
    """
    
    data = yf.download(tickers, start, end, auto_adjust=True)['Close']
    return data.dropna()

ETF Prices

In [ ]:
prices = get_etf_data(TICKERS, START_DATE, END_DATE)

In [300]:
prices.head()

Ticker            BIL         GLD         SPY        TIP         TLT
Date                                                                
2015-01-02  76.333511  114.080002  171.568039  85.979103   96.881805
2015-01-05  76.350174  115.800003  168.469574  86.047760   98.403709
2015-01-06  76.333511  117.120003  166.882721  86.055389  100.176689
2015-01-07  76.333511  116.430000  168.962341  86.124016   99.978828
2015-01-08  76.333511  115.940002  171.960556  85.986717   98.654793

### 🧮 Volatility and Weight Calculation

Functions for calculating rolling volatility and daily risk-parity weights

In [301]:
def calculate_rolling_volatility(tickers: list[str], start: str, end: str, window: int):
    """
    Calculates rolling 126-day volatility for given tickers and date range.
    
    Parameters:
        tickers (list[str]): U.S. equity ticker symbols
        start_date (str): Start date in 'YYYY-MM-DD' format
        end_date (str): End date in 'YYYY-MM-DD' format
        window (int): Length of lookback period in number of days

    Returns:
        pd.DataFrame: DataFrame with date-indexed rolling 126-day volatility
    """

    # Fetch price data
    data = get_etf_data(tickers, start, end)

    # Compute daily return
    returns = data.pct_change()

    # Compute rolling volatility
    rolling_vol = returns.rolling(window=window).std()

    return rolling_vol

In [302]:
def calculate_daily_risk_parity_weights(tickers: list[str] = TICKERS, start: str = START_DATE, end: str = END_DATE, window: int = VOL_LOOKBACK):
    """
    Calculates daily risk-parity weights for given tickers and date range.
    
    Parameters:
        tickers (list[str]): U.S. equity ticker symbols
        start (str): Start date in 'YYYY-MM-DD' format
        end (str): End date in 'YYYY-MM-DD' format
        window (int): Length of lookback period in number of days

    Returns:
        pd.DataFrame: DataFrame with date-indexed risk-parity weights
    """

    # Fetch rolling volatility
    vol = calculate_rolling_volatility(tickers, start, end, window)

    # Invert volatility
    inv_vol = 1 / vol.replace(0, np.nan)  # Replace zero vol with NaN to avoid inf

    # Normalize rows so weights sum to 1
    weights = inv_vol.div(inv_vol.sum(axis=1), axis=0)  # Fill NaN weights with zero

    return weights

Portfolio Weights

In [ ]:
portfolio_weights = calculate_daily_risk_parity_weights()

In [304]:
portfolio_weights.dropna().head()

Ticker           BIL       GLD       SPY       TIP       TLT
Date                                                        
2015-07-06  0.907820  0.017565  0.020907  0.039084  0.014624
2015-07-07  0.907393  0.017636  0.021331  0.038949  0.014691
2015-07-08  0.907950  0.017654  0.020922  0.038729  0.014745
2015-07-09  0.908240  0.017680  0.021148  0.038365  0.014567
2015-07-10  0.908204  0.017691  0.021385  0.038188  0.014531

### 📜 Backtesting

Functions for calculating risk-parity portfolio returns and performance metrics

In [305]:
def calculate_portfolio_returns(weights: pd.DataFrame, closing_prices: pd.DataFrame):
    """
    Calculates daily risk-parity portfolio returns for given weights and total-return ETF prices
    
    Parameters:
        weights (pd.DataFrame): Daily risk-parity weights of the portfolio
        closing_prices (pd.DataFrame): Daily adjusted closing price of each ETF

    Returns:
        pd.DataFrame: DataFrame with date-indexed daily returns
    """

    # Compute daily return
    returns = closing_prices.pct_change().dropna()

    # Shift weights to avoid look-ahead bias
    weights_lagged = weights.shift(1).dropna()

    # Align returns with weights
    returns = returns.loc[weights_lagged.index]

    # Calculate portfolio returns
    portfolio_returns = (weights_lagged * returns).sum(axis=1).to_frame()

    # Rename the column to 'returns'
    portfolio_returns.columns = ['returns']

    # Calculate cumulative returns
    portfolio_returns['cumulative_returns'] = (1 + portfolio_returns['returns']).cumprod()

    # Suffix asset return columns with '_return'
    returns.columns = [col + '_return' for col in returns.columns]

    return pd.concat([returns, portfolio_returns], axis=1)

In [306]:
def calculate_portfolio_metrics(portfolio_returns: pd.DataFrame, risk_free_rate: float = 0.0) -> dict:
    """
    Computes annualized return, volatility, Sharpe ratio, and max drawdown, assuming 252 trading days/year

    Parameters:
        portfolio_returns (pd.DataFrame): Daily returns of portfolio
        risk_free_rate (float): Daily risk-free rate in decimal (e.g., 0.0 or 0.0001 for 2.5% annualized)

    Returns:
        dict: Dictionary of metrics
    """

    # Calculates number of years of data
    num_years = (portfolio_returns.index[-1] - portfolio_returns.index[0]).days / 365.25

    annualized_return = float(portfolio_returns['cumulative_returns'].iloc[-1] ** (1 / num_years) - 1)

    annualized_volatility = float(portfolio_returns['returns'].std() * np.sqrt(252))

    sharpe_ratio = float(((portfolio_returns['returns'] - risk_free_rate).mean() / portfolio_returns['returns'].std()) * np.sqrt(252))

    max_drawdown = float((portfolio_returns['cumulative_returns'] / portfolio_returns['cumulative_returns'].cummax() - 1).min())

    return {
        'Annualized Return': annualized_return,
        'Annualized Volatility': annualized_volatility,
        'Sharpe Ratio': sharpe_ratio,
        'Max Drawdown': max_drawdown
    }

Function for backtesting

In [307]:
def backtest_portfolio(weights: pd.DataFrame, closing_prices: pd.DataFrame):
    """
    Backtest risk-parity portfolio by calculating portfolio metrics
    
    Parameters:
        weights (pd.DataFrame): Daily risk-parity weights of the portfolio
        closing_prices (pd.DataFrame): Daily adjusted closing price of each ETF

    Returns:
        Tuple[pd.DataFrame, dict]: Daily portfolio returns as DataFrame and summary performance metrics as a dictionary
    """

    returns = calculate_portfolio_returns(weights, closing_prices)

    metrics = calculate_portfolio_metrics(returns)

    return returns, metrics

Functions for calculating full-history and rolling VaR/CVaR

In [308]:
def calculate_full_hist_var_cvar(returns: pd.DataFrame, confidence: float = 0.95):
    """
    Calculate full-history Value-at-Risk and CVaR for given portfolio returns and confidence level
    
    Parameters:
        returns (pd.DataFrame): Daily returns of portfolio
        confidence (float): Confidence level of calculation (default to 0.95)

    Returns:
        dict[str, float]: Full-history VaR and CVaR
    """

    var = np.percentile(returns['returns'], 100 * (1 - confidence))
    cvar = returns['returns'][returns['returns'] <= var].mean()
    
    return {'VaR': float(var), 'CVaR': float(cvar)}

In [309]:
def calculate_rolling_var_cvar(returns: pd.DataFrame, period: int = 252, confidence: float = 0.95):
    """
    Calculate rolling Value-at-Risk and CVaR for given portfolio returns and confidence level
    
    Parameters:
        returns (pd.DataFrame): Daily returns of portfolio
        period (int): Length of lookback period in number of days (default to 252)
        confidence (float): Confidence level of calculation (default to 0.95)

    Returns:
        pd.DataFrame: Date-Indexed dataframe of rolling VaR and CVaR
    """

    rolling_var = []
    rolling_cvar = []

    for i in range(period, len(returns)):
        window_returns = returns[i - period:i]

        var_and_cvar = calculate_full_hist_var_cvar(window_returns)

        rolling_var.append(var_and_cvar['VaR'])
        rolling_cvar.append(var_and_cvar['CVaR'])
    
    dates = returns.index[period:]
    rolling_var_series = pd.Series(rolling_var, index = dates, name = 'VaR')
    rolling_cvar_series = pd.Series(rolling_cvar, index = dates, name = 'CVaR')

    return pd.concat([rolling_var_series, rolling_cvar_series], axis=1)

Returns and Performance Metrics

In [310]:
portfolio_returns, portfolio_metrics = backtest_portfolio(portfolio_weights, prices)

var_and_cvar = calculate_full_hist_var_cvar(portfolio_returns)

rolling_var_and_cvar = calculate_rolling_var_cvar(portfolio_returns)

In [311]:
portfolio_returns.head()

BIL_return  GLD_return  SPY_return  TIP_return  TLT_return  \
Date                                                                     
2015-07-07   -0.000219   -0.011601    0.006289    0.003287    0.009396   
2015-07-08    0.000000    0.002979   -0.016777    0.001240    0.008636   
2015-07-09    0.000000    0.002431    0.001809   -0.006456   -0.019702   
2015-07-10    0.000000    0.001167    0.012592   -0.004717   -0.015858   
2015-07-13    0.000000   -0.004485    0.011037   -0.003488   -0.003102   

             returns  cumulative_returns  
Date                                      
2015-07-07 -0.000005            0.999995  
2015-07-08 -0.000130            0.999865  
2015-07-09 -0.000460            0.999405  
2015-07-10 -0.000125            0.999280  
2015-07-13 -0.000022            0.999258

In [312]:
portfolio_metrics

{'Annualized Return': 0.021749577798811703,
 'Annualized Volatility': 0.006159362837226902,
 'Sharpe Ratio': 3.5017449614998832,
 'Max Drawdown': -0.0075904362135139625}

In [313]:
var_and_cvar

{'VaR': -0.0005421594101878612, 'CVaR': -0.0007486397601672275}

In [314]:
rolling_var_and_cvar.head()

VaR      CVaR
Date                          
2016-07-06 -0.000549 -0.000717
2016-07-07 -0.000549 -0.000717
2016-07-08 -0.000549 -0.000717
2016-07-11 -0.000549 -0.000717
2016-07-12 -0.000549 -0.000717

### 📈 Performance Plots

Functions for plotting equity curve, weights evolution, and rolling VaR and CVaR

In [315]:
def plot_equity_curve(returns: pd.DataFrame, title: str = 'Portfolio Equity Curve'):
    """
    Plot equity curve for given portfolio returns
    
    Parameters:
        portfolio_returns (pd.DataFrame): Daily returns of portfolio
    """
    
    cumulative_returns = (1 + returns['returns']).cumprod()

    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=cumulative_returns.index,
        y=cumulative_returns,
        mode='lines',
        name='Equity Curve',
        line=dict(color='green')
    ))

    fig.update_layout(
        title=title,
        xaxis_title='Date',
        yaxis_title='Cumulative Return (per $1)',
        template='plotly_white'
    )
    fig.show()

In [316]:
def plot_weights(weights: pd.DataFrame):
    """
    Plot weight evolution of each ETF over time
    
    Parameters:
        weights (pd.DataFrame): Daily risk-parity weights of the portfolio
    """
    
    fig = go.Figure()

    for col in weights.columns:
        fig.add_trace(go.Bar(
            x=weights.index,
            y=weights[col],
            name=col,
            hovertemplate=f'%{{x}}<br>{col}: %{{y:.2f}}<extra></extra>',
        ))

    fig.update_layout(
        barmode='stack',
        title=dict(
            text="Portfolio Weights over Time",
            font=dict(size=18, family="Arial Black"),
            x=0.5
        ),
        xaxis_title='Date',
        yaxis_title='Weights',
        yaxis=dict(range=[0, 1]),
        template='simple_white',
        legend=dict(
            orientation='v',
            yanchor='top',
            y=0.99,
            xanchor='left',
            x=0.01
        ),
        bargap=0,
    )

    fig.show()

In [317]:
def plot_rolling_var_and_cvar(rolling_var_and_cvar_series: pd.DataFrame):
    """
    Plot rolling VaR and CVaR

    Parameters:
        rolling_var_and_cvar_series (pd.DataFrame): Date-indexed rolling VaR and CVaR
    """
    
    # Create plot
    fig = go.Figure()

    # Add curves
    fig.add_trace(go.Scatter(x=rolling_var_and_cvar_series.index, y=rolling_var_and_cvar_series['VaR'], name='Rolling VaR (95%)'))
    fig.add_trace(go.Scatter(x=rolling_var_and_cvar_series.index, y=rolling_var_and_cvar_series['CVaR'], name='Rolling CVaR (95%)'))

    # Layout
    fig.update_layout(title="Rolling 252-Day VaR and CVaR", xaxis_title="Date", yaxis_title="Return", template="plotly_white")
    fig.show()

Plots

In [318]:
plot_equity_curve(portfolio_returns)

In [319]:
plot_weights(portfolio_weights)

In [320]:
plot_rolling_var_and_cvar(rolling_var_and_cvar)

### 🧪 Stress-Testing Under Extreme Scenarios

Stress Scenarios Parameters

In [321]:
STRESS_EVENTS: dict[str, tuple[str]] = {
    "March 2020 COVID-19 Crash (Feb-Apr 2020)": ("2020-02-19", "2020-03-23"),
    "2022 Russian-Ukraine War sell-off": ("2022-02-16", "2022-03-15"),
    "2025 Feb-April sell-off": ("2025-02-01", "2025-04-08")
}

EXTREME_SHOCK = {'SPY': -0.3, 'TLT': 0.1, 'GLD': -0.15}  # –30% equity, +10% rates move, –15% commodity move

Function for stress-testing the portfolio by recalculating returns and performance metrics

In [322]:
def stress_test_period(weights: pd.DataFrame, closing_prices: pd.DataFrame, start_date: str, end_date: str):
    """
    Backtest risk-parity portfolio by calculating portfolio metrics
    
    Parameters:
        weights (pd.DataFrame): Daily risk-parity weights of the portfolio
        closing_prices (pd.DataFrame): Daily adjusted closing price of each ETF
        start_date (str): Start of stress period (YYYY-MM-DD).
        end_date (str): End of stress period (YYYY-MM-DD).

    Returns:
        Tuple[pd.DataFrame, dict[str, float|int]]: Daily portfolio returns under stress as DataFrame and summary performance metrics as a dictionary
    """

    # Calculate portfolio's entire daily returns
    full_returns = calculate_portfolio_returns(weights, closing_prices)

    # Get portfolio's returns and cumulative returns during stress window
    stress_returns = full_returns.loc[start_date:end_date].copy()

    # Calculate portfolio's performance metrics during stress window
    stress_metrics = calculate_portfolio_metrics(stress_returns)

    # Add cumulative return into metrics
    stress_metrics['Cumulative Return'] = float(stress_returns['cumulative_returns'].iloc[-1] / stress_returns['cumulative_returns'].iloc[0] - 1)
    
    # Find pre-stress peak
    pre_stress_peak = full_returns['cumulative_returns'].loc[:start_date].max()

    # Calculate portfolio's post_stress returns
    post_stress_returns = full_returns['cumulative_returns'].loc[end_date:]

    # Calculate recovery date and time
    recovery_date = post_stress_returns[post_stress_returns >= pre_stress_peak].first_valid_index()
    recovery_time = post_stress_returns.index.get_loc(recovery_date) if recovery_date else None

    # Add metric into dictionary
    stress_metrics['Recovery Time (Trading days)'] = recovery_time

    return stress_returns, stress_metrics

Function for simulating shock

In [323]:
def simulate_shock(weights: pd.DataFrame, shock: dict[str, float], date: str | None = None):
    """
    Simulate extreme shock to estimate portfolio loss for given weights and day
    
    Parameters:
        weights (pd.DataFrame): Daily risk-parity weights of the portfolio
        shock (dict[str, float]): The shock to each asset
        date (str | None): Date of to simulate the shock for (default to first day)

    Returns:
        float: Portoflio loss from the shock
    """

    return float((weights.dropna().loc[date] * pd.Series(shock)).sum()) if date else float((weights.dropna().iloc[0] * pd.Series(shock)).sum())

Stress Returns and Performance Metrics

In [324]:
stresses_performances = {}
for event in STRESS_EVENTS:
    stress_returns, stress_metrics = stress_test_period(portfolio_weights, prices, STRESS_EVENTS[event][0], STRESS_EVENTS[event][1])
    stresses_performances[event] = (stress_returns, stress_metrics)

shock_loss = simulate_shock(portfolio_weights, EXTREME_SHOCK)

In [325]:
stresses_performances["March 2020 COVID-19 Crash (Feb-Apr 2020)"][0].head()

BIL_return  GLD_return  SPY_return  TIP_return  TLT_return  \
Date                                                                     
2020-02-19    0.000000    0.005831    0.004781   -0.000421   -0.000069   
2020-02-20    0.000000    0.004085   -0.004108    0.001937    0.007833   
2020-02-21    0.000218    0.015025   -0.010298    0.001849    0.009341   
2020-02-24   -0.000109    0.008985   -0.033166    0.004614    0.014928   
2020-02-25    0.000000   -0.017874   -0.030302   -0.001670    0.005325   

             returns  cumulative_returns  
Date                                      
2020-02-19  0.000139            1.075135  
2020-02-20  0.000163            1.075310  
2020-02-21  0.000444            1.075787  
2020-02-24 -0.000123            1.075655  
2020-02-25 -0.000665            1.074940

In [326]:
stresses_performances["March 2020 COVID-19 Crash (Feb-Apr 2020)"][1]

{'Annualized Return': 1.2105864231075856,
 'Annualized Volatility': 0.013032367741337052,
 'Sharpe Ratio': -0.5069824542936913,
 'Max Drawdown': -0.006671474945726952,
 'Cumulative Return': -0.0007761918911169952,
 'Recovery Time (Trading days)': 1}

In [327]:
stresses_performances["2022 Russian-Ukraine War sell-off"][0].head()

BIL_return  GLD_return  SPY_return  TIP_return  TLT_return  \
Date                                                                     
2022-02-16    0.000000    0.010284    0.001121    0.001948    0.005927   
2022-02-17   -0.000109    0.013668   -0.021361    0.002268    0.007438   
2022-02-18    0.000109   -0.000733   -0.006475    0.003314    0.010527   
2022-02-22    0.000000    0.002089   -0.010732    0.003061    0.002604   
2022-02-23   -0.000109    0.004507   -0.017739    0.000723   -0.013782   

             returns  cumulative_returns  
Date                                      
2022-02-16  0.000262            1.080348  
2022-02-17 -0.000007            1.080341  
2022-02-18  0.000230            1.080589  
2022-02-22  0.000032            1.080623  
2022-02-23 -0.000341            1.080255

In [328]:
stresses_performances["2022 Russian-Ukraine War sell-off"][1]

{'Annualized Return': 1.8603882887166208,
 'Annualized Volatility': 0.006069992208291945,
 'Sharpe Ratio': 1.4600271349931346,
 'Max Drawdown': -0.0017306264483649691,
 'Cumulative Return': 0.00040542611850358234,
 'Recovery Time (Trading days)': 167}

In [329]:
stresses_performances["2025 Feb-April sell-off"][0].head()

BIL_return  GLD_return  SPY_return  TIP_return  TLT_return  \
Date                                                                     
2025-02-03    0.000284    0.005337   -0.006730    0.002315    0.008142   
2025-02-04    0.000000    0.009848    0.006708    0.001663    0.003063   
2025-02-05    0.000109    0.006210    0.004055    0.004427    0.016510   
2025-02-06    0.000219   -0.002650    0.003476   -0.001744   -0.000445   
2025-02-07    0.000219    0.001784   -0.009154   -0.002667   -0.006455   

             returns  cumulative_returns  
Date                                      
2025-02-03  0.000484            1.217050  
2025-02-04  0.000391            1.217525  
2025-02-05  0.000764            1.218455  
2025-02-06  0.000116            1.218596  
2025-02-07 -0.000181            1.218375

In [330]:
stresses_performances["2025 Feb-April sell-off"][1]

{'Annualized Return': 2.1745345322362124,
 'Annualized Volatility': 0.006710632748234866,
 'Sharpe Ratio': 5.281100333331602,
 'Max Drawdown': -0.0024342971843973604,
 'Cumulative Return': 0.005998549412883358,
 'Recovery Time (Trading days)': 0}

In [331]:
print("Shock Loss:", shock_loss)

Shock Loss: -0.007444345533155537


### 📉 Stress Performance Plots

Function for plotting equity curve overlays alongisde full-history curve for all stress windows

In [332]:
def plot_equity_curve_with_stress(portfolio_returns: pd.DataFrame, stress_windows: dict[str, tuple[str]]):
    """
    Plot full equity curve with overlays for stress scenarios.

    Parameters:
        portfolio_returns (pd.DataFrame): Portfolio's entire daily returns and equity 
        stress_windows (dict[str, tuple[str]]): Dict of {label: (start_date, end_date)}
    """

    # Create plot
    fig = go.Figure()

    # Full equity curve
    fig.add_trace(go.Scatter(
        x=portfolio_returns['cumulative_returns'].index, y=portfolio_returns['cumulative_returns'].values,
        mode='lines', name='Full Equity Curve',
        line=dict(color='yellow', width=2)
    ))

    # Add stress overlays
    for label, (start, end) in stress_windows.items():
        stress_curve = portfolio_returns['cumulative_returns'].loc[start:end]

        fig.add_trace(go.Scatter(
            x=stress_curve.index,
            y=stress_curve.values,
            mode='lines',
            name=label,
            line=dict(dash='dashdot'),
        ))

    # Layout
    fig.update_layout(
        title="Equity Curve with Stress Period Overlays",
        xaxis_title="Date",
        yaxis_title="Portfolio Value",
        legend_title="Legend",
        template="plotly_white"
    )

    fig.show()

Plot

In [333]:
plot_equity_curve_with_stress(portfolio_returns, STRESS_EVENTS)

### 🦾 Proposed Enhancement: Risk-Parity Weights with Dynamic Rebalancing Frequency

Import of required package

In [334]:
import requests
import scipy

Initialization of API Token

In [335]:
Alpha_Vantage_API_TOKEN = "GBMV74GZ3G8DGXO2" # Replace with your own Alpha Vantage API token
GDP_SMOOTH_WINDOW = 315  # 15 months
GDP_SLOPE_WINDOW = 60  # 3 months
FED_SMOOTH_WINDOW = 252 # 12 months
FED_SLOPE_WINDOW = 45 # 2 months

Function for fetching Real GDP and FED Rate data

In [ ]:
def fetch_data(data_type: str, frequency: str, start_date: str = START_DATE, end_date: str = END_DATE):
    """
    Fetches data (Real GDP or FED Rates) from Alpha Vantage API for a given frequency.

    Parameters:
        data_type (str): Type of data to fetch, 'GDP' or 'FED Rates'
        frquency (str): Frequency of data, 'quarterly' or 'annual' for GDP / 'daily', 'weekly', or 'monthly' for FED rates
        start_date (str): Start date in 'YYYY-MM-DD' format (default to START_DATE)
        end_date (str): End date in 'YYYY-MM-DD' format (default to END_DATE)

    Returns:
        pd.DataFrame: DataFrame with date-/datetime-indexed data
    """

    if data_type not in ['GDP', 'FED Rates']:
        raise ValueError("Data Type must be either 'GDP' or 'FED Rates'.")
    
    if (data_type == 'GDP' and frequency not in ['quarterly', 'annual']) or (data_type == 'FED Rates' and frequency not in ['daily', 'weekly', 'monthly']):
        raise ValueError("Frequency must be either 'quarterly' or 'annual' for GDP or 'daily', 'weekly', or 'monthly' for FED rates.")

    request_function = 'REAL_GDP' if data_type == 'GDP' else 'FEDERAL_FUNDS_RATE'
    request_url = f'https://www.alphavantage.co/query?function={request_function}&interval={frequency}&apikey={Alpha_Vantage_API_TOKEN}'
    requestResponse = requests.get(request_url)

    # Check if the response is valid
    if requestResponse.status_code != 200:
        raise ValueError(f"Error fetching data.")

    # Extract Requested Data
    result = pd.DataFrame(requestResponse.json()['data'])

    # Convert 'date' column to datetime
    result["date"] = pd.to_datetime(result["date"])

    # Set 'date' as index
    result.set_index("date", inplace=True)
    
    # Ensure the DataFrame is sorted by date
    result = result.sort_index()

    # Convert the value column to numeric
    result = result.astype({'value': float})

    # Rename the column accordingly
    result.columns = ['GDP'] if data_type == 'GDP' else ['FED Rate']

    return result.loc[start_date:end_date]

Function for calculating GDP signal and FED Rates signals

In [337]:
def calculate_signal(data_type: str, data: pd.DataFrame, smooth_window: int, slope_window: int):
    """
    Estimate the trend of GDP growth for equity exposure tilt or the trend of refinancing rate for bond duration tilt

    Parameters:
        data_type (str): Type of data to fetch, 'GDP' or 'FED Rates'
        data (pd.DataFrame): Date-indexed data
        smooth_window (int): Length of smoothing window in number of days
        slope_window (int): Length of slope window in number of days

    Returns:
        pd.DataFrame: DataFrame with date-/datetime-indexed signal (-1 for falling, 0 for flat, 1 for rising)
    """

    # Interpolate GDP data to monthly
    if data_type == 'GDP':
        data = data.resample('D').asfreq().interpolate(method='spline', order=2)  # Assumes linear progresison within quarters

    # Smooth the rate using a 15-month moving average
    ma = data.rolling(window=smooth_window, min_periods=10).mean()

    # Smooth the change over a 6-month window
    slope = ma.diff().rolling(window=slope_window).mean()

    # Convert to directional signal
    signal = slope.apply(np.sign).ffill().reindex(slope.index)

    return signal

Function for calculating dynamic rebalancing weights

In [338]:
def calculate_daily_dynamic_reb_weights(weights: pd.DataFrame, gdp_sig: pd.DataFrame, fed_sig:pd.DataFrame, equity_tilt: float = 0.06, duration_tilt: float = 0.10):
    """
    Calculate dynamic rebalancing weights by applying macro overlay

    Parameters:
        wights (pd.DataFrame): Date-indexed risk-parity portfolip weights
        gdp_signal (pd.DataFrame): Directional signals from GDP data
        fed_signal (pd.DataFrame): Directional signals from FED Rates data
        equity_tilt (float): Amount of allocation to shift from/to equity ETF (default to 6%)
        duration_tilt (float): Amount of allocation to shift from/to bond ETF (default to 10%)

    Returns:
        pd.DataFrame: DataFrame with date-/datetime-indexed dynamically rebalanced weights
    """

    dynamic_reb_weights = weights.copy()
    for date in dynamic_reb_weights.index:
        if dynamic_reb_weights.loc[date].isna().any():
            continue

        d_signal = fed_sig['FED Rate'].loc[date] if date in fed_sig.index else 0
        e_signal = gdp_sig['GDP'].loc[date] if date in gdp_sig.index else 0

        # Apply Equity Tilt
        dynamic_reb_weights.loc[date, 'SPY'] += e_signal * equity_tilt
        for col in dynamic_reb_weights.columns:
            if col != 'SPY':
                dynamic_reb_weights.loc[date, col] -= e_signal * (equity_tilt / (len(dynamic_reb_weights.columns) - 1))


        # Apply Duration Tilt
        dynamic_reb_weights.loc[date, 'TLT'] += d_signal * duration_tilt
        dynamic_reb_weights.loc[date, 'TIP'] -= d_signal * duration_tilt

        # Normalize weights to sum to 1 and clip negatives
        row = dynamic_reb_weights.loc[date].clip(lower=0)
        dynamic_reb_weights.loc[date] = row / row.sum() if row.sum() > 0 else row

    return dynamic_reb_weights

Macro Signals

In [339]:
gdp_data = fetch_data('GDP', 'quarterly')
gdp_signals = calculate_signal('GDP', gdp_data, GDP_SMOOTH_WINDOW, GDP_SLOPE_WINDOW)

In [340]:
gdp_signals.dropna().head()

GDP
date           
2015-03-11  1.0
2015-03-12  1.0
2015-03-13  1.0
2015-03-14  1.0
2015-03-15  1.0

In [341]:
fed_rates = fetch_data('FED Rates', 'daily')
fed_signals = calculate_signal('FED Rates', fed_rates, FED_SMOOTH_WINDOW, FED_SLOPE_WINDOW)

In [342]:
fed_signals.dropna().head()

FED Rate
date                
2015-02-24       1.0
2015-02-25       1.0
2015-02-26      -1.0
2015-02-27      -1.0
2015-02-28      -1.0

Dynamically Rebalanced Weights

In [343]:
dynamic_reb_portfolio_weights = calculate_daily_dynamic_reb_weights(portfolio_weights, gdp_signals, fed_signals)

In [359]:
dynamic_reb_portfolio_weights.dropna().head()

Ticker           BIL       GLD       SPY  TIP       TLT
Date                                                   
2015-07-06  0.829823  0.002384  0.075198  0.0  0.092595
2015-07-07  0.829322  0.002450  0.075583  0.0  0.092645
2015-07-08  0.829670  0.002466  0.075188  0.0  0.092677
2015-07-09  0.829659  0.002489  0.075372  0.0  0.092480
2015-07-10  0.829490  0.002499  0.075580  0.0  0.092431

Dynamically Rebalaned Portfolio Returns and Performance Metrics

In [345]:
dynamic_reb_portfolio_returns, dynamic_reb_portfolio_metrics = backtest_portfolio(dynamic_reb_portfolio_weights, prices)

dynamic_reb_var_and_cvar = calculate_full_hist_var_cvar(dynamic_reb_portfolio_returns)

dynamic_reb_rolling_var_and_cvar = calculate_rolling_var_cvar(dynamic_reb_portfolio_returns)

In [346]:
dynamic_reb_portfolio_returns.head()

BIL_return  GLD_return  SPY_return  TIP_return  TLT_return  \
Date                                                                     
2015-07-07   -0.000219   -0.011601    0.006289    0.003287    0.009396   
2015-07-08    0.000000    0.002979   -0.016777    0.001240    0.008636   
2015-07-09    0.000000    0.002431    0.001809   -0.006456   -0.019702   
2015-07-10    0.000000    0.001167    0.012592   -0.004717   -0.015858   
2015-07-13    0.000000   -0.004485    0.011037   -0.003488   -0.003102   

             returns  cumulative_returns  
Date                                      
2015-07-07  0.001134            1.001134  
2015-07-08 -0.000461            1.000672  
2015-07-09 -0.001684            0.998987  
2015-07-10 -0.000515            0.998473  
2015-07-13  0.000536            0.999009

In [347]:
dynamic_reb_portfolio_metrics

{'Annualized Return': 0.025657085049945128,
 'Annualized Volatility': 0.015217803096521902,
 'Sharpe Ratio': 1.674907032835825,
 'Max Drawdown': -0.04453592084600688}

In [348]:
dynamic_reb_var_and_cvar

{'VaR': -0.0015183177094732618, 'CVaR': -0.0022107612317264795}

In [349]:
dynamic_reb_rolling_var_and_cvar.head()

VaR      CVaR
Date                          
2016-07-06 -0.001336 -0.002109
2016-07-07 -0.001336 -0.002109
2016-07-08 -0.001336 -0.002109
2016-07-11 -0.001278 -0.002079
2016-07-12 -0.001278 -0.002079

Performance Plots

In [350]:
plot_equity_curve(dynamic_reb_portfolio_returns, title='Dynamically Rebalanced Portfolio Equity Curve')

In [351]:
plot_weights(dynamic_reb_portfolio_weights)

In [352]:
plot_rolling_var_and_cvar(dynamic_reb_rolling_var_and_cvar)